In [3]:
import sys
sys.executable

'/Users/yibinlin/.pyenv/versions/3.10.12/envs/huggingface_test/bin/python3.10'

In [4]:
!type python

python is /Users/yibinlin/.pyenv/versions/huggingface_test/bin/python


In [5]:
%pip install bertviz


[notice] A new release of pip is available: 23.1.2 -> 23.2.1
[notice] To update, run: python3.10 -m pip install --upgrade pip
Note: you may need to restart the kernel to use updated packages.


In [6]:
from transformers import AutoTokenizer
from bertviz.transformers_neuron_view import BertModel
from bertviz.neuron_view import show

In [7]:
model_ckpt = "bert-base-uncased"
tokenizer = AutoTokenizer.from_pretrained(model_ckpt)
model = BertModel.from_pretrained(model_ckpt)

In [8]:
a = "test"
print(a)

test


In [9]:
text = "fruit flies like banana."
show(model, "bert", tokenizer, text, display_mode="light", layer=0, head=8)

<IPython.core.display.Javascript object>

<IPython.core.display.Javascript object>

In [10]:
inputs = tokenizer(text, return_tensors="pt", add_special_tokens=False)
inputs.input_ids

tensor([[ 5909, 10029,  2066, 15212,  1012]])

In [11]:
from torch import nn
from transformers import AutoConfig

config = AutoConfig.from_pretrained(model_ckpt)
token_emb = nn.Embedding(config.vocab_size, config.hidden_size)
token_emb

Embedding(30522, 768)

In [12]:
inputs_embeds = token_emb(inputs.input_ids)
inputs_embeds.size()

torch.Size([1, 5, 768])

In [13]:
import torch
from math import sqrt

query = key = value = inputs_embeds
dim_k = key.size(-1)
# Note key needs to be transposed here.
scores = torch.bmm(query, key.transpose(1, 2)) / sqrt(dim_k)
scores

tensor([[[27.0267,  0.0963,  0.0775, -0.0472,  0.7827],
         [ 0.0963, 29.1460, -1.7396,  0.9850, -1.1843],
         [ 0.0775, -1.7396, 27.1871, -1.9561, -0.3089],
         [-0.0472,  0.9850, -1.9561, 26.9691, -0.8605],
         [ 0.7827, -1.1843, -0.3089, -0.8605, 29.8677]]],
       grad_fn=<DivBackward0>)

In [14]:
dim_k

768

In [15]:
import torch.nn.functional as F

weights = F.softmax(scores, dim=-1)
# this will be equal to 1 in every row (?), i.e. the sum of all columns will be 1.
weights.sum(dim=-1)
weights

tensor([[[1.0000e+00, 2.0149e-12, 1.9774e-12, 1.7457e-12, 4.0029e-12],
         [2.4203e-13, 1.0000e+00, 3.8598e-14, 5.8862e-13, 6.7256e-14],
         [1.6843e-12, 2.7370e-13, 1.0000e+00, 2.2041e-13, 1.1445e-12],
         [1.8491e-12, 5.1906e-12, 2.7410e-13, 1.0000e+00, 8.1989e-13],
         [2.3364e-13, 3.2679e-14, 7.8427e-14, 4.5177e-14, 1.0000e+00]]],
       grad_fn=<SoftmaxBackward0>)

In [16]:
value.size()

torch.Size([1, 5, 768])

In [17]:
attn_outputs = torch.bmm(weights, value)
attn_outputs.size()

torch.Size([1, 5, 768])

In [18]:
def scaled_dot_product_attention(query, key, value):
    dim_k = query.size(-1)
    scores = torch.bmm(query, key.transpose(1, 2))
    weights = F.softmax(scores, dim=-1)
    return torch.bmm(weights, value)

In [19]:
class AttentionHead(nn.Module):
    def __init__(self, embed_dim, head_dim):
        super().__init__()
        self.q = nn.Linear(embed_dim, head_dim)
        self.k = nn.Linear(embed_dim, head_dim)
        self.v = nn.Linear(embed_dim, head_dim)

    def forward(self, hidden_state):
        attn_outputs = scaled_dot_product_attention(
            self.q(hidden_state), self.k(hidden_state), self.v(hidden_state)
        )
        return attn_outputs

In [20]:
class MultiHeadAttention(nn.Module):
    def __init__(self, config):
        super().__init__()
        embed_dim = config.hidden_size
        num_heads = config.num_attention_heads
        head_dim = embed_dim // num_heads
        self.heads = nn.ModuleList(
            [AttentionHead(embed_dim, head_dim) for _ in range(num_heads)]
        )
        self.output_linear = nn.Linear(embed_dim, embed_dim)
    
    def forward(self, hidden_state):
        x = torch.cat([h(hidden_state) for h in self.heads], dim=-1)
        x = self.output_linear(x)
        return x

In [23]:
multihead_attn = MultiHeadAttention(config)
attn_output = multihead_attn(inputs_embeds)
attn_output.size()

torch.Size([1, 5, 768])

In [24]:
from bertviz import head_view
from transformers import AutoModel

model = AutoModel.from_pretrained(model_ckpt, output_attentions=True)

sentence_a = "time flies like an arrow"
sentence_b = "fruit flies like a banana"

viz_inputs = tokenizer(sentence_a, sentence_b, return_tensors="pt")
attention = model(**viz_inputs).attentions
sentence_b_start = (viz_inputs.token_type_ids == 0).sum(dim=1)
tokens = tokenizer.convert_ids_to_tokens(viz_inputs.input_ids[0])

head_view(attention, tokens, sentence_b_start, heads=[8])

huggingface/tokenizers: The current process just got forked, after parallelism has already been used. Disabling parallelism to avoid deadlocks...
To disable this warning, you can either:
	- Avoid using `tokenizers` before the fork if possible
	- Explicitly set the environment variable TOKENIZERS_PARALLELISM=(true | false)


Some weights of the model checkpoint at bert-base-uncased were not used when initializing BertModel: ['cls.predictions.transform.LayerNorm.weight', 'cls.predictions.bias', 'cls.predictions.transform.dense.weight', 'cls.predictions.transform.LayerNorm.bias', 'cls.predictions.transform.dense.bias', 'cls.seq_relationship.weight', 'cls.seq_relationship.bias']
- This IS expected if you are initializing BertModel from the checkpoint of a model trained on another task or with another architecture (e.g. initializing a BertForSequenceClassification model from a BertForPreTraining model).
- This IS NOT expected if you are initializing BertModel from the checkpoint of a model that you expect to be exactly identical (initializing a BertForSequenceClassification model from a BertForSequenceClassification model).


<IPython.core.display.Javascript object>

In [25]:
config.intermediate_size

3072

In [26]:
config.hidden_size

768

In [27]:
config.hidden_dropout_prob

0.1

In [28]:
class FeedForward(nn.Module):
    def __init__(self, config):
        super().__init__()
        self.linear_1 = nn.Linear(config.hidden_size, config.intermediate_size)
        self.linear_2 = nn.Linear(config.intermediate_size, config.hidden_size)
        self.gelu = nn.GELU()
        self.dropout = nn.Dropout(config.hidden_dropout_prob)

    def forward(self, x):
        x = self.linear_1(x)
        x = self.gelu(x)
        x = self.linear_2(x)
        # dropout: https://pytorch.org/docs/stable/generated/torch.nn.Dropout.html
        # during training ,randomly zeroes some of the elements of the input 
        # tensor with probability p using samples from a Bernoulli distribution.
        # Each cahannel will be zeroed out independntly on every forward calll.
        x = self.dropout(x)
        return x

## More about Dropout / Bernoulli distribution
A Bernoulli distribution is just a fancy way of saying a coin toss (coin can be unfair coin), with binary outcome.

In [30]:
# feed forward call
feed_forward = FeedForward(config)
ff_outputs = feed_forward(attn_outputs)
ff_outputs.size()

torch.Size([1, 5, 768])

In [31]:
# Layer Normalization pp. 71, using prelayer normalization
class TransformerEncoderLayer(nn.Module):
    def __init__(self, config):
        super().__init__()
        self.layer_norm_1 = nn.LayerNorm(config.hidden_size)
        self.layer_norm_2 = nn.LayerNorm(config.hidden_size)
        self.attention = MultiHeadAttention(config)
        self.feed_forward = FeedForward(config)
    
    def forward(self, x):
        # Apply layer normalization and then copy input into query, key, value
        # query, key , value have their separate learned parameter metrics, see 
        # definition of AttentionHead class before.
        hidden_state = self.layer_norm_1(x)
        # Apply attention with a skip connection
        x = x + self.attention(hidden_state)
        # Apply feed-forward layer with a skip connection
        x = x + self.feed_forward(self.layer_norm_2(x))
        return x

## Layer Normalization concepts

"layer normalization is like telling a neural network not to worry too much about the exact values its neurons output, but instead to focus on their relative differences. It achieves this by 'normalizing', or adjusting, the outputs of each neuron in a layer so that, overall, they have a standard (average) value, and a standard amount of variation."

In [32]:
# testing run
encoder_layer = TransformerEncoderLayer(config)
inputs_embeds.shape, encoder_layer(inputs_embeds).size()

(torch.Size([1, 5, 768]), torch.Size([1, 5, 768]))

## Note
The self-attention and feed-forward layers are said to be invariant to the position of the tokens..
There is an easy trick to incorporate positional information using positional embeddings.

In [34]:
config.max_position_embeddings

512

In [54]:
input_ids_debug = inputs.input_ids
input_ids_debug

tensor([[ 5909, 10029,  2066, 15212,  1012]])

In [58]:
# unsqueeze: https://pytorch.org/docs/stable/generated/torch.unsqueeze.html
# Returns a new tensor with a dimension of size one inserted at the specified position.
# Specifically, in the following code, it turns the tensor of size [5] to [1, 5]
position_ids_debug = torch.arange(5, dtype=torch.long).unsqueeze(0)
position_ids_debug

tensor([[0, 1, 2, 3, 4]])

In [59]:
# Positional Embeddings implementation
class Embeddings(nn.Module):
    def __init__(self, config):
        super().__init__()
        self.token_embeddings = nn.Embedding(config.vocab_size, config.hidden_size)
        self.position_embeddings = nn.Embedding(config.max_position_embeddings, config.hidden_size)
        # eps: a value added to denominator for numerical stsability. Default 1e-5.
        self.layer_norm = nn.LayerNorm(config.hidden_size, eps=1e-12)
        self.dropout = nn.Dropout()
    
    def forward(self, input_ids):
        # Create position IDs for input sequence
        seq_length = input_ids.size(1)
        position_ids = torch.arange(seq_length, dtype=torch.long).unsqueeze(0)
        # Create token and position embeddings
        token_embeddings = self.token_embeddings(input_ids)
        position_embeddigns = self.position_embeddings(position_ids)
        # Combine token and position embeddings
        embeddings = token_embeddings + position_embeddigns
        embeddings = self.layer_norm(embeddings)
        embeddings = self.dropout(embeddings)
        return embeddings

embedding_layer = Embeddings(config)
embedding_layer(inputs.input_ids).size()

torch.Size([1, 5, 768])

In [60]:
config.num_hidden_layers

12

In [64]:
# embeddings are called out once, combining token and position embeddings.
class TransformerEncoder(nn.Module):
    def __init__(self, config):
        super().__init__()
        self.embeddings = Embeddings(config)
        self.layers = nn.ModuleList([TransformerEncoderLayer(config)
                                     for _ in range(config.num_hidden_layers)])
        
    def forward(self, x):
        x = self.embeddings(x)
        for layer in self.layers:
            x = layer(x)
        return x

In [65]:
encoder = TransformerEncoder(config)
encoder(inputs.input_ids).size()

torch.Size([1, 5, 768])

In [66]:
config.hidden_dropout_prob

0.1

In [67]:
config.num_labels

2

## Adding a Classification Head

Transformer models are usually divided into a task-independent body and a task-specific head.

In [71]:
class TransformerForSequenceClassification(nn.Module):
    def __init__(self, config):
        super().__init__()
        self.encoder = TransformerEncoder(config)
        self.dropout = nn.Dropout(config.hidden_dropout_prob)
        self.classifier = nn.Linear(config.hidden_size, config.num_labels)
    
    def forward(self, x):
        x = self.encoder(x)[:, 0, :] # select hidden state of [CLS] token, i.e. first token
        x = self.dropout(x)
        x = self.classifier(x)
        return x

In [73]:
config.num_labels = 3
encoder_classifier = TransformerForSequenceClassification(config)
encoder_classifier(inputs.input_ids)

tensor([[0.1595, 0.0291, 1.6171]], grad_fn=<AddmmBackward0>)

# The Decoder
